In [ ]:
import pandas as pd # type: ignore
import json
import glob

files = glob.glob("../phasetwo/2025-06-18/log-parquet/*.parquet")
structured = open("error.06-18.log", "w", encoding="utf-8")
for log in files:
    df = pd.read_parquet(log)
    # df = pd.read_parquet("../data/sample/normal/log-parquet/" + log)
    print(f"Processing {log} with {len(df)} records")

    # 逐行打印message列的内容
    for index, row in df.iterrows():
        if 'message' in row:
            message = row['message']
            if not message.startswith('{"'):
                continue
            message = json.loads(message)
            if 'error' in message:
                structured.write(f"Row {index}: {message}\n")
            # elif 'session' in message:
            #     print(message['session'])
        else:
            print(row)
# print(f"k8_namespace\t{row['k8_namespace']}\ntimestamp\t{row['@timestamp']}\nagent_name\t{row['agent_name']}\nk8_pod\t{row['k8_pod']}\nmessage\t{row['message']}\nk8_node_name\t{row['k8_node_name']}")
# print(row)

In [1]:
import pandas as pd
import json
import glob
import os

# Find all date folders (assuming they follow the pattern ../phasetwo/YYYY-MM-DD/)
date_folders = glob.glob("../phasetwo/*/")  # Gets all directories in phasetwo

for date_folder in date_folders:
    # Extract date from folder path (assuming format ../phasetwo/YYYY-MM-DD/)
    date = os.path.basename(os.path.normpath(date_folder))

    # Skip if not in YYYY-MM-DD format
    if len(date) != 10 or date[4] != '-' or date[7] != '-':
        continue

    # Find all parquet files for this date
    parquet_files = glob.glob(f"{date_folder}/log-parquet/*.parquet")

    if not parquet_files:
        print(f"No parquet files found for date {date}")
        continue

    # Create error log file for this date
    error_log_path = f"error-{date}.log"
    print(f"Processing date {date}, output to {error_log_path}")

    with open(error_log_path, "w", encoding="utf-8") as structured:
        for log_file in parquet_files:
            try:
                df = pd.read_parquet(log_file)
                print(f"  Processing {os.path.basename(log_file)} with {len(df)} records")

                for index, row in df.iterrows():
                    if 'message' in row:
                        message = row['message']
                        if not isinstance(message, str) or not message.startswith('{"'):
                            continue
                        try:
                            message_json = json.loads(message)
                            if 'error' in message_json:
                                structured.write(f"File: {os.path.basename(log_file)}, Row {index}: {message_json}\n")
                        except json.JSONDecodeError:
                            continue
            except Exception as e:
                print(f"Error processing {log_file}: {str(e)}")

    print(f"Finished processing date {date}\n")

Processing date 2025-06-20, output to error-2025-06-20.log
  Processing log_filebeat-server_2025-06-20_18-00-00.parquet with 401160 records
  Processing log_filebeat-server_2025-06-20_20-00-00.parquet with 382684 records
  Processing log_filebeat-server_2025-06-20_15-00-00.parquet with 355380 records
  Processing log_filebeat-server_2025-06-20_02-00-00.parquet with 141808 records
  Processing log_filebeat-server_2025-06-20_12-00-00.parquet with 320925 records
  Processing log_filebeat-server_2025-06-20_05-00-00.parquet with 156744 records
  Processing log_filebeat-server_2025-06-20_21-00-00.parquet with 298488 records
  Processing log_filebeat-server_2025-06-20_19-00-00.parquet with 582851 records
  Processing log_filebeat-server_2025-06-20_11-00-00.parquet with 458782 records
  Processing log_filebeat-server_2025-06-20_07-00-00.parquet with 149028 records
  Processing log_filebeat-server_2025-06-20_03-00-00.parquet with 121292 records
  Processing log_filebeat-server_2025-06-20_01-00-

In [ ]:
import re
import glob
import json
from drain3 import TemplateMiner
from drain3.file_persistence import FilePersistence
from drain3.template_miner_config import TemplateMinerConfig

config = TemplateMinerConfig()
config.load("exp/template/drain3_log.ini")
persistence = FilePersistence("drain3_state.json")
template_miner = TemplateMiner(persistence, config)

template_clusters = {}

files = glob.glob("logs/error-*.log")
for log_file in files:
    with open(log_file, 'r') as f:
        for line in f:
            json_part = re.sub(r'^File: [^,]*, Row \d+: ', '', line.strip())
            error = json.loads(json_part)['error']
            result = template_miner.add_log_message(error)

            if result["change_type"] != "none":
                print(" Log Parings Result: " + json.dumps(result))
            if result['cluster_id'] not in template_clusters:
                template_clusters[result['cluster_id']] = 0
            template_clusters[result['cluster_id']] += 1
print(f"Total clusters: {len(template_clusters)}")
output = []
for cluster_id, count in template_clusters.items():
    output.append({
        "cluster_id": cluster_id,
        "count": count
    })

output.sort(key=lambda x: x["count"], reverse=True)
for i, item in enumerate(output):
    print(f"Cluster {i}: ID {item['cluster_id']}, Count {item['count']}")

{'error': 'failed to complete the order: rpc error: code = Internal desc = failed to prepare order: failed to get product #"LS4PSXUNUM"', 'http.req.id': '5af8350d-b892-4a43-aa2a-8b300c739873', 'http.req.method': 'POST', 'http.req.path': '/cart/checkout', 'message': 'request error', 'session': 'e3a393d1-b8dd-49e7-b58d-e9217aa0be46', 'severity': 'error', 'timestamp': '2025-06-20T10:11:07.118266264Z'}
{'error': 'could not retrieve product: rpc error: code = Unknown desc = Error 9005 (HY000): Region is unavailable', 'http.req.id': '7a6021a4-6f92-4ce2-8048-d67bc2ad1004', 'http.req.method': 'GET', 'http.req.path': '/product/LS4PSXUNUM', 'message': 'request error', 'session': '4b359621-0cb5-4567-b8dd-569d84b998d3', 'severity': 'error', 'timestamp': '2025-06-20T10:11:07.307143136Z'}
{'error': 'could not retrieve product: rpc error: code = Unknown desc = Error 9005 (HY000): Region is unavailable', 'http.req.id': '686c6910-f683-4797-9a0b-e490f71c0370', 'http.req.method': 'GET', 'http.req.path': 

KeyboardInterrupt: 

In [7]:
import pandas as pd
import json
import glob
import re

def normalize_error(error: str) -> str:
    if not isinstance(error, str):
        return error

    # 先替换以#开头的ID
    error = re.sub(r'#\w+', '<PRODUCT_ID>', error)

    # 再替换不带#的产品ID，假设是8-12位大写字母数字组合
    error = re.sub(r'\b[A-Z0-9]{8,12}\b', '<PRODUCT_ID>', error)

    return error

error_logs = []
files = glob.glob("../phasetwo/*/log-parquet/*.parquet")  # Gets all directories in phasetwo
for file in files:
    try:
        df = pd.read_parquet(file)
        print(f"Processing {file} with {len(df)} records")

        for index, row in df.iterrows():
            if 'message' in row:
                message = row['message']
                if not isinstance(message, str) or not message.startswith('{"'):
                    continue
                try:
                    message_json = json.loads(message)
                    if 'error' in message_json:
                        msg = normalize_error(message_json['error'])
                        if msg not in error_logs:
                            error_logs.append(msg)
                            print(msg)
                except json.JSONDecodeError:
                    continue
    except Exception as e:
        print(f"Error processing {log_file}: {str(e)}")
# with open("error_logs.txt", "w", encoding="utf-8") as error_logs:
#     error_logs.write("\n".join(error_logs))

Processing ../phasetwo/2025-06-20/log-parquet/log_filebeat-server_2025-06-20_11-00-00.parquet with 458782 records
failed to complete the order: rpc error: code = Internal desc = failed to charge card: could not charge the card: rpc error: code = Unavailable desc = connection error: desc = "transport: Error while dialing dial tcp 10.233.55.4:50051: connect: connection refused"
Processing ../phasetwo/2025-06-20/log-parquet/log_filebeat-server_2025-06-20_22-00-00.parquet with 155634 records
Processing ../phasetwo/2025-06-20/log-parquet/log_filebeat-server_2025-06-20_06-00-00.parquet with 127235 records
could not retrieve product: rpc error: code = Unknown desc = Error 9005 (HY000): Region is unavailable
failed to complete the order: rpc error: code = Internal desc = failed to prepare order: failed to get product #"<PRODUCT_ID>"
failed to get product recommendations: failed to get recommended product info (<PRODUCT_ID>): rpc error: code = Unknown desc = Error 9005 (HY000): Region is unavai

KeyboardInterrupt: 

In [ ]:
import re
from drain3 import TemplateMiner
from drain3.file_persistence import FilePersistence
from drain3.template_miner_config import TemplateMinerConfig

logs = [
    'failed to get ads: rpc error: code = DeadlineExceeded desc = context deadline exceeded',
    'failed to get product recommendations: rpc error: code = Unknown desc = Exception calling application: <_InactiveRpcError of RPC that terminated with:\n\tstatus = StatusCode.UNAVAILABLE\n\tdetails = "Connection reset by peer"\n\tdebug_error_string = "{"created":"@1750145456.221303383","description":"Error received from peer ipv4:10.233.54.177:3550","file":"src/core/lib/surface/call.cc","file_line":1055,"grpc_message":"Connection reset by peer","grpc_status":14}"\n>',
    'failed to complete the order: rpc error: code = Canceled desc = context canceled',
    'failed to complete the order: rpc error: code = Unavailable desc = transport is closing',
    "failed to add to cart: rpc error: code = FailedPrecondition desc = Can't access cart storage.",
    'failed to complete the order: rpc error: code = Internal desc = failed to prepare order: failed to get product #"6E92ZMYYFZ"',
    'failed to get product recommendations: rpc error: code = Canceled desc = context canceled',
    'could not retrieve currencies: rpc error: code = Canceled desc = context canceled',
    'failed to do currency conversion for product L9ECAV7KIM: rpc error: code = Canceled desc = context canceled',
    'failed to get shipping quote: failed to convert currency for shipping cost: rpc error: code = Canceled desc = context canceled',
    'could not convert currency for product #1YMWWN1N4O: rpc error: code = Canceled desc = context canceled',
    'failed to complete the order: rpc error: code = Internal desc = failed to prepare order: failed to convert price of "2ZYFJ3GM2N" to EUR',
    'failed to get ads: rpc error: code = Unavailable desc = connection error: desc = "transport: Error while dialing dial tcp 10.233.8.174:9555: connect: connection refused"',
    'failed to get ads: rpc error: code = DeadlineExceeded desc = context deadline exceeded',
    "failed to add to cart: rpc error: code = FailedPrecondition desc = Can't access cart storage.",
    'could not retrieve product: rpc error: code = Unknown desc = Error 9005 (HY000): Region is unavailable',
    'failed to get product recommendations: failed to get recommended product info (#1YMWWN1N4O): rpc error: code = Unknown desc = Error 9005 (HY000): Region is unavailable',
    "failed to add to cart: rpc error: code = FailedPrecondition desc = Can't access cart storage.",
    'failed to complete the order: rpc error: code = Internal desc = failed to prepare order: failed to get product #"OLJCESPC7Z"',
    'could not retrieve product: rpc error: code = Unknown desc = Error 9001 (HY000): PD server timeout: start timestamp may fall behind safe point',
    'failed to get product recommendations: failed to get recommended product info (#7JSJCESPC9H): rpc error: code = Unknown desc = Error 9001 (HY000): PD server timeout: start timestamp may fall behind safe point',
    'failed to complete the order: rpc error: code = Internal desc = cart failure: failed to get user cart during checkout: rpc error: code = Unavailable desc = connection error: desc = "transport: Error while dialing dial tcp: lookup cartservice on 10.233.33.139:53: server misbehaving"',
    "could not retrieve cart: rpc error: code = FailedPrecondition desc = Can't access cart storage. StackExchange.Redis.RedisTimeoutException: Timeout awaiting response (outbound=0KiB, inbound=0KiB, 5575ms elapsed, timeout is 5000ms), command=HGET, next: HGET 1dc31007-9289-45cb-a5f2-5953d34d1543, inst: 0, qu: 0, qs: 2, aw: False, bw: Inactive, rs: ReadAsync, ws: Idle, in: 0, in-pipe: 0, out-pipe: 0, last-in: 349, cur-in: 0, sync-ops: 2, async-ops: 1620, serverEndpoint: redis-cart:6379, conn-sec: 2785.32, aoc: 1, mc: 1/1/0, mgr: 10 of 10 available, clientName: cartservice-2(SE.Redis-v2.6.122.38350), IOCP: (Busy=0,Free=1000,Min=1,Max=1000), WORKER: (Busy=1,Free=32766,Min=1,Max=32767), POOL: (Threads=4,QueuedItems=0,CompletedItems=43675,Timers=4), v: 2.6.122.38350"
]

config = TemplateMinerConfig()
config.load("template/drain3_log.ini")
persistence = FilePersistence("drain3_state.bin")
template_miner = TemplateMiner(persistence, config)
pattern = re.compile(r'(?P<prefix>.*?)(?P<segment>rpc error: code = [^:]+? desc = (?:(?!rpc error:).)+)', re.IGNORECASE)

templates = {}
for log_line in logs:
    # result = template_miner.add_log_message(log_line)
    # template = result["template_mined"]
    # if template:
    #     templates[template] = templates.get(template, 0) + 1
    matches = list(pattern.finditer(log_line))
    print("Original log:")
    print(log_line)
    print("Split into:")
    for i, m in enumerate(matches):
        prefix = m.group("prefix") if i == 0 else ""
        segment = m.group("segment")
        print("•", prefix + segment)

# # 打印排序后的模板
# for i, (tmpl, count) in enumerate(sorted(templates.items(), key=lambda x: -x[1])):
#     print(f"[{count} occurrences] {tmpl}")

Original log:
failed to get ads: rpc error: code = DeadlineExceeded desc = context deadline exceeded
Split into:
• failed to get ads: rpc error: code = DeadlineExceeded desc = context deadline exceeded
Original log:
failed to get product recommendations: rpc error: code = Unknown desc = Exception calling application: <_InactiveRpcError of RPC that terminated with:
	status = StatusCode.UNAVAILABLE
	details = "Connection reset by peer"
	debug_error_string = "{"created":"@1750145456.221303383","description":"Error received from peer ipv4:10.233.54.177:3550","file":"src/core/lib/surface/call.cc","file_line":1055,"grpc_message":"Connection reset by peer","grpc_status":14}"
>
Split into:
• failed to get product recommendations: rpc error: code = Unknown desc = Exception calling application: <_InactiveRpcError of RPC that terminated with:
Original log:
failed to complete the order: rpc error: code = Canceled desc = context canceled
Split into:
• failed to complete the order: rpc error: code =